In [1]:
import os
os.chdir('/Users/ngdnh/Codespace/PulsatingPulseShop/')

import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning) 

%config InlineBackend.figure_formats = ['svg']

In [2]:
import qiskit
from qiskit_ibm_runtime import QiskitRuntimeService
import utility as ut
import qutip as qt 
import numpy as np
import pickle 
import matplotlib.pyplot as plt
import json
import datetime
from qiskit_ibm_runtime import SamplerV2 as Sampler
from qiskit_ibm_runtime import Batch
from scipy.stats import norm
from scipy.stats import gaussian_kde

In [3]:
plt.rcParams['axes.linewidth'] = 1.0
%config InlineBackend.figure_formats = ['svg']
today = datetime.datetime.now()

print(today)

2025-01-31 23:30:33.831734


# IQ clusters

In this notebook, we find the relative positions of the $|0\rangle, |1\rangle, |2\rangle$ clusters on the IQ plane.

## The experiment

In [4]:
service = QiskitRuntimeService()
print(service.backends())
backend = service.backend('ibm_brisbane')

qubit = 109
clbit = 0

num_qubits = int(qubit+1)
num_clbits = 1

weight = 1

rough_01_freq = backend.defaults().qubit_freq_est[qubit]
qubit_anharmonicty = backend.properties().qubits[qubit][3].value * 1e9
rough_12_freq = rough_01_freq + qubit_anharmonicty

print('Chosen backend', backend)
print(r"f01 = "+f'{round(rough_01_freq/1e9, 4)}'+' GHz')
print(r'f12 = '+f'{round(rough_12_freq/1e9, 4)}'+' GHz')
print(r'anharmonicity = '+f'{round(qubit_anharmonicty/1e9, 4)}'+' GHz')

[<IBMBackend('ibm_brisbane')>, <IBMBackend('ibm_sherbrooke')>, <IBMBackend('ibm_kyiv')>]
Chosen backend <IBMBackend('ibm_brisbane')>
f01 = 4.985 GHz
f12 = 4.6779 GHz
anharmonicity = -0.3071 GHz


### Helper function

In [5]:
def pulse12_sched(sx12_params):
    """ 
        Args:
            `amp`: Rabi amplitude
        Return:
            `schedule`: Corresponding schedule for the Rabi 12 pulse with chosen `amp`.
    """
    with qiskit.pulse.build(backend=backend) as schedule:
        drive_chan = qiskit.pulse.drive_channel(qubit)
        qiskit.pulse.set_frequency(rough_12_freq, drive_chan)
        qiskit.pulse.play(qiskit.pulse.Drag(duration=sx12_params['dur'], amp=sx12_params['amp'], sigma=int(sx12_params['dur']/4), beta=sx12_params['beta']), drive_chan)
        
    return schedule

We first create a circuit that prepares the state $|0\rangle$. This means we turn on the qubit, and wait for it to relax to the ground state. 

In [6]:
ground_circ = qiskit.circuit.QuantumCircuit(num_qubits, num_clbits)
ground_circ.measure(qubit, clbit)

The circuit that prepares the state $|1\rangle$ employs the $\pi$ pulse on the $01$ subspace. We can reliably use the default $\pi$ pulse provided by IBM Quantum.

In [7]:
first_exc_circ = qiskit.circuit.QuantumCircuit(num_qubits, num_clbits)
first_exc_circ.x(qubit)
first_exc_circ.measure(qubit, clbit)

Finally, the circuit that prepares the state $|2\rangle$ employs another $\pi$ pulse on the $12$ subspace. We have calibrated this pulse, so we call the results from Rabi oscilation. We add a reset gate at the end.

In [8]:
with open("./x12_params.json", "r") as json_file:
    x12_params = json.load(json_file)

x12_params

{'freq': 4677855926.141399, 'dur': 40, 'amp': 0.47272727272727266, 'beta': 0}

In [9]:
pi12_gate = qiskit.circuit.Gate('pi12', 1, [])

second_exc_circ = qiskit.circuit.QuantumCircuit(num_qubits, num_clbits)
second_exc_circ.x(qubit)
second_exc_circ.append(pi12_gate, [qubit])
second_exc_circ.measure(qubit, clbit)
second_exc_circ.append(pi12_gate, [qubit])
second_exc_circ.add_calibration(pi12_gate, [qubit], pulse12_sched(x12_params))

We will have 10k shots

In [10]:
num_shots = 10000

### Sampler & Job

In this experiment, we try running jobs in batch...

In [11]:
sampler = Sampler(backend)
 
sampler.options.default_shots = num_shots
sampler.options.execution.meas_type = "kerneled"
sampler.options.execution.rep_delay = 0.0005

In [63]:
with Batch(backend=backend) as batch:
    ground_job = sampler.run([ground_circ])
    first_exc_job = sampler.run([first_exc_circ])
    second_exc_job = sampler.run([second_exc_circ])

In [69]:
print(f'Job ID {ground_job.job_id()} status: {ground_job.status()}')
print(f'Job ID {first_exc_job.job_id()} status: {first_exc_job.status()}')
print(f'Job ID {second_exc_job.job_id()} status: {second_exc_job.status()}')

Job ID cy22fmycw2k0008jg8m0 status: DONE
Job ID cy22fne6vek0008rbv8g status: DONE
Job ID cy22wdh9b62g008h80y0 status: DONE


### Saving kerneled data

In [70]:
job = second_exc_job

In [71]:
job_params = {'backend': backend, 'qubit': qubit, 'job_id_string': job.job_id(), 'datetime': datetime.datetime.now(), 'num_shots': num_shots,
                   'delay_overlap': True, 'mapping_01': True, 'rep_delay': sampler.options.execution.rep_delay, 'extended_delay': 0, 'idling_circuits': False, 'unconditional_reset12': True} 

path = "./characterization/discrim/data/" 
folder_name = job.job_id()
full_path = os.path.join(path, folder_name)

os.mkdir(full_path)

with open(f"./{full_path}/params.pkl", "wb") as f:
    pickle.dump(job_params, f)

In [72]:
job_result = ut.DataAnalysis(experiment=job, average=False, shots=num_shots, qubit=0)
job_result.retrieve_data(average=False)

with open(f"./{full_path}/iq_data.pkl", "wb") as f:
    pickle.dump(job_result.IQ_data, f)

## Data processing

In [4]:
experiment_ids = ['cy22fmycw2k0008jg8m0', 'cy22fne6vek0008rbv8g', 'cy22wdh9b62g008h80y0']

iq_data_list = []

for id in experiment_ids:
    path = f"./characterization/discrim/data/{id}"
    iq_data = np.array(np.load(f"{path}/iq_data.pkl", allow_pickle=True))
    iq_data_list.append(iq_data)

iq_data_list = np.array(iq_data_list)

In [6]:
fig, axes = plt.subplots(ncols=3, figsize=(12, 4))
colors = ['red', 'blue', 'green']
for i in [0, 1, 2]:
    axes[i].scatter(np.real(iq_data_list[i]), np.imag(iq_data_list[i]), s=1, color=colors[i])
    axes[i].set_xlim([-90, 70])
    axes[i].set_ylim([-40, 120])

x0, y0 = -35, 30
x1, y1 = 32, 32
x2, y2 = 22, 6
rad = 30

axes[0].axvline(x0)
axes[0].axvline(x0-rad, linestyle='--')
axes[0].axvline(x0+rad, linestyle='--')
axes[0].axhline(y0)
axes[0].axhline(y0+rad, linestyle='--')
axes[0].axhline(y0-rad, linestyle='--')

axes[1].axvline(x1)
axes[1].axvline(x1-rad, linestyle='--')
axes[1].axvline(x1+rad, linestyle='--')
axes[1].axhline(y1)
axes[1].axhline(y1+rad, linestyle='--')
axes[1].axhline(y1-rad, linestyle='--')

axes[2].axvline(x2)
axes[2].axvline(x2-rad, linestyle='--')
axes[2].axvline(x2+rad, linestyle='--')
axes[2].axhline(y2)
axes[2].axhline(y2+rad, linestyle='--')
axes[2].axhline(y2-rad, linestyle='--')

fig.tight_layout()

In [7]:
central_clusters = np.array([
    [x0, y0], [x1, y1], [x2, y2]
])

np.save('./central_clusters', central_clusters, allow_pickle=True)

From these graphs, I define three regions on the IQ plane

In [14]:
def discrim(IQpoint):
    d0 = np.sqrt((np.real(IQpoint)-x0)**2+(np.imag(IQpoint)-y0)**2)
    d1 = np.sqrt((np.real(IQpoint)-x1)**2+(np.imag(IQpoint)-y1)**2)
    d2 = np.sqrt((np.real(IQpoint)-x2)**2+(np.imag(IQpoint)-y2)**2)
    lab = {'0': d0, '1': d1, '2': d2}
    smallest_label = min(lab, key=lab.get)
    
    return smallest_label, lab[smallest_label]

In [15]:
discrim((40+20*1j))

('1', np.float64(12.806248474865697))

In [41]:
IQdata_0_classified = np.zeros(len(iq_data_list[0][0]), dtype=tuple)

for idx, IQpoint in enumerate(iq_data_list[0][0]):
    label, _ = discrim(IQpoint)
    IQdata_0_classified[idx] = (IQpoint, label)

p00 = []
p01 = []
p02 = []
for point in IQdata_0_classified:
    if point[1] == '0':
        p00.append(point[0])
    elif point[1] == '1':
        p01.append(point[0])
    else:
        p02.append(point[0])

In [44]:
IQdata_1_classified = np.zeros(len(iq_data_list[1][0]), dtype=tuple)

for idx, IQpoint in enumerate(iq_data_list[1][0]):
    label, _ = discrim(IQpoint)
    IQdata_1_classified[idx] = (IQpoint, label)

p10 = []
p11 = []
p12 = []
for point in IQdata_1_classified:
    if point[1] == '0':
        p10.append(point[0])
    elif point[1] == '1':
        p11.append(point[0])
    else:
        p12.append(point[0])

In [45]:
IQdata_2_classified = np.zeros(len(iq_data_list[2][0]), dtype=tuple)

for idx, IQpoint in enumerate(iq_data_list[2][0]):
    label, _ = discrim(IQpoint)
    IQdata_2_classified[idx] = (IQpoint, label)

p20 = []
p21 = []
p22 = []
for point in IQdata_2_classified:
    if point[1] == '0':
        p20.append(point[0])
    elif point[1] == '1':
        p21.append(point[0])
    else:
        p22.append(point[0])

In [48]:
fig, axes = plt.subplots(ncols=3, figsize=(12, 4))
colors = ['red', 'blue', 'green']

for i in [0, 1, 2]:
    axes[i].set_xlim([-90, 70])
    axes[i].set_ylim([-40, 120]) 

axes[0].scatter(np.real(p00), np.imag(p00), s=1, color=colors[0])
axes[0].scatter(np.real(p01), np.imag(p01), s=1, color=colors[1])
axes[0].scatter(np.real(p02), np.imag(p02), s=1, color=colors[2])

axes[1].scatter(np.real(p10), np.imag(p10), s=1, color=colors[0])
axes[1].scatter(np.real(p11), np.imag(p11), s=1, color=colors[1])
axes[1].scatter(np.real(p12), np.imag(p12), s=1, color=colors[2])

axes[2].scatter(np.real(p20), np.imag(p20), s=1, color=colors[0])
axes[2].scatter(np.real(p21), np.imag(p21), s=1, color=colors[1])
axes[2].scatter(np.real(p22), np.imag(p22), s=1, color=colors[2])

fig.tight_layout()

In [51]:
confusion_matrix = np.array([
    [len(p00)/num_shots, len(p01)/num_shots, len(p02)/num_shots],
    [len(p10)/num_shots, len(p11)/num_shots, len(p12)/num_shots],
    [len(p20)/num_shots, len(p21)/num_shots, len(p22)/num_shots]
])

confusion_matrix

array([[0.9771, 0.0184, 0.0045],
       [0.0188, 0.889 , 0.0922],
       [0.0218, 0.1629, 0.8153]])

In [52]:
np.save('./confusion_matrix', confusion_matrix, allow_pickle=True)